In [4]:
# encoding: utf-8
# Original code from https://gist.github.com/nathanielatom/6442f94faca69dcf6efae146cb66c30c

In [1]:
import bokeh.models as bkm
import resampy
from BokehAudioPlayer import AudioPlayerModel
from bokeh.plotting import figure, output_file, show
from bokeh.layouts import layout
from bokeh import palettes
import base64
from io import BytesIO
import numpy as np
from scipy.io import wavfile
import pandas as pd

from bokeh.io import output_notebook
output_notebook()


/Users/russell/anaconda/lib/python3.5/site-packages/numba/errors.py:102: UserWarning: Insufficiently recent colorama version found. Numba requires colorama >= 0.3.9
  warnings.warn(msg)


Loading BokehJS ...

In [4]:
# Load data
datadir = '../data/'
datastr = 'LD.CPNY.2020-02-09.2020-05-07.5_15Hz_1min.BHZ'
# datastr = 'CI.USC.2020-02-09.2020-05-05.5_15Hz.BHZ'
# datastr = 'MAJO_M7.3_BHZ'
datafile = datadir+datastr+'.csv'
outfile = './'
TargetDuration = 50  # seconds

# Load seismogram into dataframe
# df = pd.read_csv(datafile, names=['data'])
df = pd.read_csv(datafile, parse_dates=['t_cent'])
df
dt = (df.t_cent[1]-df.t_cent[0]).seconds  # time between samples
fs = 1/dt  # [Hz] sample rate

# # # Calculate daily averages using boxcar window
# dt_hr = dt/60/60  # Hours between samples
# df['daily_average'] = df.disp_avg.rolling(int(24/dt_hr),win_type='boxcar').mean()

# Replace huge outliers (earthquakes?) with daily average value
df.disp_avg[df.disp_avg > 1e-8] = df.daily_average[df.disp_avg > 1e-8]

# Fill nan values with mean value
df.daily_average = df.daily_average.fillna(df.daily_average.mean())
df.disp_avg = df.disp_avg.fillna(df.disp_avg.mean())

# Subtract daily signal
df.data = df.disp_avg - df.daily_average

# Seismic data in units of displacement
data = np.asarray(df.data)*1e9  # convert meters to nanometers

# 1) force the signal's mean value to be zero (to protect your loudspeakers...)
data = data - np.mean(data)

# store data in units of displacemnt for plotting
data_dis = data

# 2) limit the signal's amplitude = avoid too large peaks (how to re-kill your loudspeakers...)
# a simple way is to normalize the data according to its maximum amplitude value
# data = data/np.amax(data) # This is dangerous, peak values can be negative, too
# better to do it THIS way:  
data = data/np.amax(np.absolute(data))

# Set up title names
default_title=datastr  # will become output file name
title='NYC seismic noise daily average removed (02-09 to 05-07-2020)'
plot_filename=default_title + '_' + str(TargetDuration) + 's' + '.html'

# make plot and sonify
# grid = AudioPlayerModel.sonify_plotwf(data=data,data_dis=data_dis,fs=fs,TargetDuration=TargetDuration,
#                                       fs_resamp=44100,default_title=default_title,title=title)
grid = AudioPlayerModel.sonify_plotwfspec(data=data,data_dis=data_dis,fs=fs,TargetDuration=TargetDuration,
                                      fs_resamp=44100,default_title=default_title,title=title,
                                      aspect_ratio=2,  # aspect ratio of individual plots
                                      # palette='RdYlBu11'
                                      palette = palettes.all_palettes['Magma'][256],
                                      seek_bar_color='limegreen',
                                      seek_bar_alpha=0.8,
                                      ywav_axis_label_true='Ground Displacement',
                                      x_axis_label_true = 'True Time (days)',
                                      # palette='Viridis256'
                                      time_true_factor = 3600*24,
                                      )

output_file(outfile+plot_filename+'test.html')
# show(grid)
show(grid)

/Users/russell/anaconda/lib/python3.5/site-packages/ipykernel/__main__.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/russell/anaconda/lib/python3.5/site-packages/ipykernel/__main__.py:29: UserWarning: Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access
